In [18]:
# Import data
import pandas as pd
import altair as alt
prices = pd.read_csv('../00_source/btc_prices_all.csv')
prices.sort_values(by='time', ascending=True, inplace=True)
social = pd.read_csv('../00_source/btc_social.csv')
social.sort_values(by='time', ascending=True, inplace=True)

# Remove Duplicate Values in Prices and Social
For some reason, we grabbed duplicate rows for both prices and social. This might actually be a problem with the CryptoCompare API.  
**We need to be aware of this problem if we implement trading algo with the API**

In [19]:
# Drop duplicates for prices
prices.drop_duplicates(inplace=True)
# Make sure there are no more duplicate time rows
prices[prices.time.isin(prices.time.value_counts()[prices.time.value_counts() > 1].index)]
# Investigate the last row
prices[prices.time == '2021-11-04 19:00:00']
# Price was still changing - the hour hasn't ended
# Remove the row
prices = prices[prices.time != '2021-11-04 19:00:00']


In [20]:
# Drop duplicates for social
social.drop_duplicates(inplace=True)
# Check
social[social.time.isin(social.time.value_counts()[social.time.value_counts() > 1].index)]


Empty DataFrame
Columns: [time, comments, posts, followers, points, overview_page_views, analysis_page_views, markets_page_views, charts_page_views, trades_page_views, forum_page_views, influence_page_views, total_page_views, fb_likes, fb_talking_about, twitter_followers, twitter_following, twitter_lists, twitter_favourites, twitter_statuses, reddit_subscribers, reddit_active_users, reddit_posts_per_hour, reddit_posts_per_day, reddit_comments_per_hour, reddit_comments_per_day, code_repo_stars, code_repo_forks, code_repo_subscribers, code_repo_open_pull_issues, code_repo_closed_pull_issues, code_repo_open_issues, code_repo_closed_issues, code_repo_contributors]
Index: []

[0 rows x 34 columns]

# Clean Social Data
- The CryptoCompare columns (first few) are cumulative
    - Create incremental versions  
<br>
- CryptoCompare columns don't seem to get a lot of interactions per hour for comments, posts, followers
    - Maybe use daily for those instead    
<br>    
- FB and Twitter data is broken - delete

- Reddit data is hourly and looks very good

- CodeRepo data is snapshot rather than hourly
    - Do we need it since it's more professional?
    - Some columns are messy - might not be worth the effort
    - Stars, forks, subscribes could be useful


In [21]:
# Create incremental versions of cryptoCompare columns
# And then drop the cumulative versions
cryptoCompareColumns = ['comments', 'posts', 'followers', 'points','overview_page_views', 'analysis_page_views', 'markets_page_views','charts_page_views', 'trades_page_views', 'forum_page_views','influence_page_views', 'total_page_views']
for col in cryptoCompareColumns:
    newColName = 'cc_' + col + '_incremental'
    social[newColName] = social[col].diff()
    social.drop(columns=col, inplace=True)


In [22]:
# See if CC variables should be hourly or daily
cryptoCompareColumns = ['cc_comments_incremental', 'cc_posts_incremental','cc_followers_incremental', 'cc_points_incremental','cc_overview_page_views_incremental','cc_analysis_page_views_incremental','cc_markets_page_views_incremental', 'cc_charts_page_views_incremental','cc_trades_page_views_incremental', 'cc_forum_page_views_incremental','cc_influence_page_views_incremental','cc_total_page_views_incremental']
for col in cryptoCompareColumns:
    avg = social[col].dropna().mean()
    print(col,': ',avg)

cc_comments_incremental :  9.85305
cc_posts_incremental :  2.0927
cc_followers_incremental :  1.356
cc_points_incremental :  184.748
cc_overview_page_views_incremental :  553.6512
cc_analysis_page_views_incremental :  8.6379
cc_markets_page_views_incremental :  9.7226
cc_charts_page_views_incremental :  128.0492
cc_trades_page_views_incremental :  6.0837
cc_forum_page_views_incremental :  161.4258
cc_influence_page_views_incremental :  0.40675
cc_total_page_views_incremental :  867.97715


In [23]:
base = alt.Chart(social.iloc[5000:10000,:]).mark_line().encode(
    x='time',
    y=alt.Y('cc_comments_incremental', scale=alt.Scale(zero=False))
).properties(width=1500).display()

# Let's use hourly for now because of the extra information we can keep

alt.Chart(...)

In [24]:
# Drop FB and Twitter columns
columnsToDrop = ['fb_likes', 'fb_talking_about', 'twitter_followers','twitter_following', 'twitter_lists', 'twitter_favourites','twitter_statuses']
social.drop(columns=columnsToDrop, inplace=True)

In [25]:
# Create incremental versions of CodeRepo columns
codeRepoColumns = ['code_repo_stars', 'code_repo_forks', 'code_repo_subscribers','code_repo_open_pull_issues', 'code_repo_closed_pull_issues','code_repo_open_issues', 'code_repo_closed_issues','code_repo_contributors']
for col in codeRepoColumns:
    newColName = col + '_incremental'
    social[newColName] = social[col].diff()
    social.drop(columns=col, inplace=True)

# Drop columns that don't make sense
columnsToDrop = ['code_repo_open_pull_issues_incremental','code_repo_closed_pull_issues_incremental','code_repo_open_issues_incremental','code_repo_closed_issues_incremental','code_repo_contributors_incremental']
social.drop(columns=columnsToDrop, inplace=True)

In [26]:
# The per day columns for reddit are just per_hour x 24
# Delete them
columnsToDrop = ['reddit_posts_per_day', 'reddit_comments_per_day']
social.drop(columns=columnsToDrop, inplace=True)

In [27]:
social.head()

time  reddit_subscribers  reddit_active_users  \
24011  2019-07-25 12:00:00             1089264                 4025   
24012  2019-07-25 13:00:00             1089299                 4184   
24013  2019-07-25 14:00:00             1089350                 4229   
24014  2019-07-25 15:00:00             1089392                 4208   
24015  2019-07-25 16:00:00             1089438                 4091   

       reddit_posts_per_hour  reddit_comments_per_hour  \
24011                   6.11                     63.77   
24012                   6.31                    121.33   
24013                   6.12                    129.22   
24014                   6.42                    117.53   
24015                   6.60                    195.44   

       cc_comments_incremental  cc_posts_incremental  \
24011                      NaN                   NaN   
24012                      9.0                   3.0   
24013                     20.0                  11.0   
24014                     28.0                   5.0   
24015                     24.0                  10.0   

       cc_followers_incremental  cc_points_incremental  \
24011                       NaN                    NaN   
24012                       1.0                  190.0   
24013                      11.0                  750.0   
24014                       4.0                  505.0   
24015                       3.0                  565.0   

       cc_overview_page_views_incremental  cc_analysis_page_views_incremental  \
24011                                 NaN                                 NaN   
24012                               765.0                                18.0   
24013                              1119.0                                28.0   
24014                               880.0                                17.0   
24015                               873.0                                25.0   

       cc_markets_page_views_incremental  cc_charts_page_views_incremental  \
24011                                NaN                               NaN   
24012                               16.0                             248.0   
24013                               17.0                             321.0   
24014                               15.0                             243.0   
24015                               22.0                             228.0   

       cc_trades_page_views_incremental  cc_forum_page_views_incremental  \
24011                               NaN                              NaN   
24012                              27.0                            259.0   
24013                              22.0                            395.0   
24014                              12.0                            352.0   
24015                               9.0                            330.0   

       cc_influence_page_views_incremental  cc_total_page_views_incremental  \
24011                                  NaN                              NaN   
24012                                  0.0                           1333.0   
24013                                  1.0                           1903.0   
24014                                  0.0                           1519.0   
24015                                  0.0                           1487.0   

       code_repo_stars_incremental  code_repo_forks_incremental  \
24011                          NaN                          NaN   
24012                          0.0                         -1.0   
24013                          0.0                          1.0   
24014                          0.0                          0.0   
24015                          0.0                          2.0   

       code_repo_subscribers_incremental  
24011                                NaN  
24012                                0.0  
24013                                0.0  
24014                                0.0  
24015                                0.0

In [28]:
prices.head()

time      open      high       low     close  \
28013  2019-07-25 11:00:00  10097.72  10109.73  10079.39  10099.63   
28014  2019-07-25 12:00:00  10099.63  10172.47  10097.14  10156.02   
28015  2019-07-25 13:00:00  10156.02  10156.02   9951.85   9983.32   
28016  2019-07-25 14:00:00   9983.32  10011.28   9967.85   9982.71   
28017  2019-07-25 15:00:00   9982.71  10018.61   9980.07   9999.98   

       volumefrom     volumeto fiat  
28013      744.52   7528865.62  USD  
28014     1784.66  18085841.44  USD  
28015     4997.00  49943817.52  USD  
28016     1211.88  12109315.88  USD  
28017     1158.29  11578467.83  USD

In [29]:
# Join prices with cleaned social
merged = pd.merge(prices, social, on='time', how = 'inner', validate='1:1')

In [30]:
# rename columns
merged.rename(columns={'volumefrom':'volume_btc', 'volumeto':'volume_fiat'}, inplace=True)

In [31]:
merged.to_csv("../20_intermediate_files/btc_prices_social_cleaned.csv", index=False)